### Author: Akshay Ijantkar
### Team: Aqua Wizards
### Project: Surfers Bible

* https://launchschool.com/books/sql/read/table_relationships

### CRONTAB Script:
0 1 * * * /usr/bin/python3 /home/ubuntu/pop_db_sch_ss/Daily_Scheduler_Swell_Pollution_Astro_News_API.py >> /home/ubuntu/pop_db_sch_ss/log_Daily_Scheduler_Swell_Pollution_Astro_News_API.txt 2>&1

# Import Libraries:

In [2]:
import pandas as pd
import numpy as np
import random
import matplotlib as plt
from matplotlib import pyplot
# import seaborn as sns; sns.set()
# from scipy.stats import norm 
import matplotlib.pyplot as plt
# For Linear regression
# from sklearn.linear_model import LinearRegression
# For split given dataset into train and test set.
# from sklearn.model_selection import train_test_split
# To verify models using this metrics 
# from sklearn.metrics import mean_squared_error, r2_score

# import statsmodels.formula.api as smf
# from sklearn.linear_model import LinearRegression
# from sklearn import metrics
# v
from matplotlib import rcParams
# rcParams['figure.figsize'] = 50,50
# import pandas_profiling
pd.set_option('display.max_rows', 1500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 1000)
from pandas import ExcelWriter
from pandas import ExcelFile

# from pygeocoder import Geocoder

import sys
# from weather_au import api
# from weather_au import summary
# from weather import place, observations, uv_index
import time

import json
import requests
from datetime import datetime, timedelta
# from catboost import CatBoostClassifier
# from sklearn.model_selection import train_test_split

# from sklearn.metrics import r2_score
# from keras.models import Sequential
# from keras.layers import Dense
# from keras.wrappers.scikit_learn import KerasRegressor
# from sklearn.model_selection import cross_val_score
# from sklearn.model_selection import KFold
# from sklearn.model_selection import cross_validate

# import catboost as ctb
# from catboost import CatBoostRegressor, FeaturesData, Pool
# from scipy.stats import uniform as sp_randFloat
# from scipy.stats import randint as sp_randInt
# from scipy.stats import uniform
# from sklearn.model_selection import RandomizedSearchCV
# from sklearn.metrics.pairwise import cosine_similarity
# from  sklearn.metrics.pairwise import euclidean_distances
# from sklearn.metrics.pairwise import manhattan_distances
# from sklearn.metrics.pairwise import pairwise_distances
import re
# import pprint
from datetime import date
import datetime
# import sqlite3
# from sqlite3 import Error
from datetime import datetime
from dateutil import tz
import datetime

%matplotlib inline

# Give Date:

In [63]:
from datetime import datetime
import datetime
no_days_from_today = 3
# User defined date otherwise default it will take 3 dates from current date
select_date = ""

if select_date == "":    
    today = date.today()
    today_date = today.strftime("%Y-%m-%d") 
    given_date =  str((datetime.datetime.strptime(today_date, "%Y-%m-%d") + datetime.timedelta(days = no_days_from_today)).date())
    print("today_date = ", today_date)
    print("given_date = ", given_date)
else:
    given_date = select_date
    print("given_date = ", given_date)
# print("today_date = ", today_date)


today_date =  2020-06-03
given_date =  2020-06-06


# Import Beach Table to DF: 

In [6]:
import psycopg2 as ps

# define credentials 
credentials = {'POSTGRES_ADDRESS' : 'test-surfers-bible-instance.cljoljhkgpfb.ap-southeast-2.rds.amazonaws.com', # change to your endpoint
               'POSTGRES_PORT' : 5432, # change to your port
               'POSTGRES_USERNAME' : '', # change to your username
               'POSTGRES_PASSWORD' : '', # change to your password
               'POSTGRES_DBNAME' : 'test_surfers_bible_db'} # change to your db name

# create connection and cursor    
conn = ps.connect(host=credentials['POSTGRES_ADDRESS'],
                  database=credentials['POSTGRES_DBNAME'],
                  user=credentials['POSTGRES_USERNAME'],
                  password=credentials['POSTGRES_PASSWORD'],
                  port=credentials['POSTGRES_PORT'])

cur = conn.cursor()

beach_df = pd.read_sql_query("SELECT * FROM BEACH_TABLE;", conn)

conn.close()

cur.close()

# beach_df.head()

# API KEYS:

# UTILITY FUNCTIONS:

In [8]:
#  Input: Datatime string
# Output: Unix time epochs in seconds (As integer)

def get_unix_time_epochs(datetime_str):
    return int(time.mktime(time.strptime(str(datetime_str), '%Y-%m-%dT%H:%M:%S')))

In [9]:
# Input: 
# from_datetime_str -> datetime string which you want to convert from one time zone to other
# from_timezone_str -> from timezone of location from which you want to convert
# to_timezone_str -> tp timezone of the location to which you want to convert
# datetime_format -> format of incoming datetime

# Output: Converted datetime of give to_timezone_str location

def convert_datetime_in_dif_timezones(from_datetime_str, from_timezone_str, to_timezone_str, 
                                      datetime_format = '%Y-%m-%dT%H:%M:%S'):
#     USE pytz.all_timezones to get all timestamps
    from datetime import datetime
    import pytz
    date_time_obj = datetime.strptime(from_datetime_str, datetime_format)
#     print("date_time_obj = ", date_time_obj)
    
    old_timezone = pytz.timezone(from_timezone_str)
    new_timezone = pytz.timezone(to_timezone_str)
    
    new_timezone_timestamp = old_timezone.localize(date_time_obj).astimezone(new_timezone).strftime("%Y-%m-%dT%H:%M:%S") 
#     print("new_timezone_timestamp", new_timezone_timestamp)
    return str(new_timezone_timestamp)
    

# SWELL DATA:

# SWELL: API CALLS:

### Make Data Swell DF:

In [28]:
swell_col_lst = [
    'date',
    'beach_id',
    'beach_name',
    'beach_latitude',
    'beach_longitude',
    'beach_state',    
    "beach_municipality",
    
    'airTemperature',
    'cloudCover',
    'currentDirection',
    'currentSpeed',
    'gust',
    'humidity',
    'precipitation',
    'pressure',
    'seaLevel',
    'secondarySwellDirection',
    'secondarySwellHeight',
    'secondarySwellPeriod',
    'swellDirection',
    'swellHeight',
    'swellPeriod',
    'time',
    'visibility',
    'waterTemperature',
    'waveDirection',
    'waveHeight',
    'wavePeriod',
    'windDirection',
    'windSpeed',
    'windWaveDirection',
    'windWaveHeight',
    'windWavePeriod'
]
swell_df = pd.DataFrame(columns = swell_col_lst
                         )
# swell_df

## Convert API response JSON dict to DF row:

In [30]:
# %%time
# Wall time: 5min 48s
import datetime
for api_limit, api_no in zip(range(0,200,50) ,range(5,9)):
    print("++++++++++++++++++++++++++++++++++++++++++++")
    API_KEY = SG_API_KEY_DICT[str(api_no)]
    print("SWELL: api_limit = ", api_limit)
    print("api_no = ", api_no)
    print("++++++++++++++++++++++++++++++++++++++++++++")
    
    for index, row in beach_df.loc[api_limit  : api_limit + 50,].iterrows():
        print("")
        print("index = ", index)
        print("beach_name", row["beach_name"])
        print(" ")

        latitude = row['beach_latitude']
        longitude = row['beach_longitude']

        start_date = given_date
        end_date = str((datetime.datetime.strptime(given_date, "%Y-%m-%d") + datetime.timedelta(days = 1)).date())
#         end_date = '2020-06-07'
        
        url_str = "https://api.stormglass.io/v2/weather/point?"
        url_str += "lat="+ str(latitude) +"&"
        url_str += "lng="+str(longitude) + "&"
        url_str += "start=" + start_date + "&"
        url_str += "end="+ end_date + "&"
        url_str += "params=waterTemperature,wavePeriod,waveDirection,waveHeight,windWaveDirection,windWaveHeight,windWavePeriod,swellPeriod,secondarySwellPeriod,swellDirection,secondarySwellDirection,swellHeight,secondarySwellHeight,windSpeed,windDirection,airTemperature,precipitation,gust,cloudCover,humidity,pressure,visibility,currentSpeed,currentDirection,seaLevel"

        payload = {}
        headers = {
          'Authorization': API_KEY
        }

        response = requests.request("GET", url_str, headers=headers, data = payload)
        response_dict = json.loads(response.text)    
    #     print("response_dict = ", response_dict)
        swell_dict = {}

        for hour_dict in response_dict['hours']:
    #         print("hour_dict = ", hour_dict)

            swell_dict['date'] = given_date
            for beach_col in beach_df.columns.tolist():
                swell_dict[beach_col] = row[beach_col]     

            swell_col_lst = list(hour_dict.keys())
            swell_col_lst.remove("time")

            for swell_col in swell_col_lst:

                swell_dict[swell_col] = hour_dict[swell_col]['sg']

            swell_dict['time'] = hour_dict['time']

            swell_df = swell_df.append(swell_dict, ignore_index=True)
###################################################################################################################


++++++++++++++++++++++++++++++++++++++++++++
SWELL: api_limit =  0
api_no =  5
++++++++++++++++++++++++++++++++++++++++++++

index =  0
beach_name ADDISCOT BEACH
 

index =  1
beach_name APEX BEACH
 

index =  2
beach_name BACK BEACH
 

index =  3
beach_name BANCOORA BEACH
 

index =  4
beach_name BARRY BEACH
 

index =  5
beach_name BARRYS BEACH
 

index =  6
beach_name BAY BEACH
 

index =  7
beach_name BELL BEACH
 

index =  8
beach_name BELLS BEACH
 

index =  9
beach_name BERRY BEACH
 

index =  10
beach_name BETKA BEACH
 

index =  11
beach_name BIDDLES BEACH
 

index =  12
beach_name BIRDROCK BEACH
 

index =  13
beach_name BIRRELLS BEACH
 

index =  14
beach_name BLACK BEACH
 

index =  15
beach_name BOOMANGONG BEACH
 

index =  16
beach_name BOUCHIERS BEACH
 

index =  17
beach_name BOURKES BEACH NO. 1
 

index =  18
beach_name BOURKES BEACH NO. 2
 

index =  19
beach_name BOURKES BEACH NO. 3
 

index =  20
beach_name BREENS BEACH
 

index =  21
beach_name BRENTNALLS BEACH
 




index =  182
beach_name TRUES BEACH
 

index =  183
beach_name TURRAS BEACH
 

index =  184
beach_name ULUPNA BEACH
 

index =  185
beach_name WEISS BEACH
 

index =  186
beach_name WESTERN BEACH
 

index =  187
beach_name WESTERN PARK BEACH
 

index =  188
beach_name WHITES BEACH
 

index =  189
beach_name WILD DOG BEACH
 

index =  190
beach_name WILD DOG SHORE
 

index =  191
beach_name WILLOW BEACH
 

index =  192
beach_name WILSONS BEACH
 

index =  193
beach_name WOODSIDE BEACH
 

index =  194
beach_name WOOLAMAI SURF BEACH
 

index =  195
beach_name WOOLLEY BEACH
 

index =  196
beach_name WRECK BEACH
 

index =  197
beach_name YANAKIE BEACH
 

index =  198
beach_name ZINETTIS BEACH NO. 1
 

index =  199
beach_name ZINETTIS BEACH NO. 2
 


# CONVERT UTC TIME TO AUSTRALIA TIME:

In [31]:
swell_df['time'] = swell_df['time'].apply(lambda x: convert_datetime_in_dif_timezones(from_datetime_str = x, 
                                                                                  from_timezone_str = 'UTC', 
                                                                                  to_timezone_str ='Australia/Melbourne', 
                                                                                datetime_format = '%Y-%m-%dT%H:%M:%S+00:00'))

# Function to impute missing values using Random Forest:

In [41]:
# Input: 
# df -> Dataframe where imputation you want
# features_lst -> features to use from df for imputation
# target_lst -> target column for which you wnat to do imputation
# Output -> DF after missing value imputation

def missing_imputation_rf_func(df, 
                               feature_lst = [
                                                'beach_latitude', 
                                                'beach_longitude', 
                                                'airTemperature', 
                                                'cloudCover', 
                                                'gust', 
                                                'humidity', 
                                                'precipitation', 
                                                'pressure',
                                                'waterTemperature', 
                                                'waveDirection', 
                                                'waveHeight', 
                                                'wavePeriod',
                                           ],
                              target_lst = [
                                                'waterTemperature', 
                                                'waveDirection', 
                                                'waveHeight', 
                                                'wavePeriod',                               
                                          ]):
    miss_impu_df = df[feature_lst].copy()    
    from missingpy import MissForest
    imputer = MissForest()
    X_imputed = imputer.fit_transform(miss_impu_df.values)
    aft_miss_imp_df = pd.DataFrame(
                      X_imputed, 
                      columns = feature_lst) 
    for col in target_lst:    
        df[col] = aft_miss_imp_df[col].values
        df[col] = df[col].apply(lambda x: round(x, 2))
    return df

# Imputing missing values:

In [44]:

try:
    swell_df = missing_imputation_rf_func(swell_df)
except:
    pass

C:\Users\aksha\Anaconda3\lib\site-packages\missingpy\missforest.py:528: UserWarning: No missing value located; returning original dataset.
  warnings.warn("No missing value located; returning original "


# Imputing missing values if above methods doesnt works:

In [45]:
try:
    swell_df['watertemperature'].fillna((swell_df['watertemperature'].mean()), inplace=True)
    swell_df['wavedirection'].fillna((swell_df['wavedirection'].mean()), inplace=True)
    swell_df['waveHeight'].fillna((swell_df['waveHeight'].mean()), inplace=True)
    swell_df['wavePeriod'].fillna((swell_df['wavePeriod'].mean()), inplace=True)
except:
    pass

# CREATE SEA_WATER_QUALITY_TABLE:

In [46]:
import psycopg2 as ps

# define credentials 
credentials = {'POSTGRES_ADDRESS' : 'test-surfers-bible-instance.cljoljhkgpfb.ap-southeast-2.rds.amazonaws.com', # change to your endpoint
               'POSTGRES_PORT' : 5432, # change to your port
               'POSTGRES_USERNAME' : '', # change to your username
               'POSTGRES_PASSWORD' : '', # change to your password
               'POSTGRES_DBNAME' : 'test_surfers_bible_db'} # change to your db name

# create connection and cursor    
conn = ps.connect(host=credentials['POSTGRES_ADDRESS'],
                  database=credentials['POSTGRES_DBNAME'],
                  user=credentials['POSTGRES_USERNAME'],
                  password=credentials['POSTGRES_PASSWORD'],
                  port=credentials['POSTGRES_PORT'])

cur = conn.cursor()

# cur.execute("DROP TABLE SEA_WATER_QUALITY_TABLE;")

create_table_query = '''
      CREATE TABLE IF NOT EXISTS SWELL_TABLE
      (
        swell_id SERIAL PRIMARY KEY,
        date DATE,
        beach_id INTEGER,
        beach_name TEXT,
        beach_latitude REAL,
        beach_longitude REAL,
        beach_state TEXT,
        beach_municipality TEXT,
        airTemperature REAL,
        cloudCover REAL,
        currentDirection REAL,
        currentSpeed REAL,
        gust REAL,
        humidity REAL,
        precipitation REAL,
        pressure REAL,
        seaLevel REAL,
        secondarySwellDirection REAL,
        secondarySwellHeight REAL,
        secondarySwellPeriod REAL,
        swellDirection REAL,
        swellHeight REAL,
        swellPeriod REAL,
        time TEXT,
        visibility REAL,
        waterTemperature REAL,
        waveDirection REAL,
        waveHeight REAL,
        wavePeriod REAL,
        windDirection REAL,
        windSpeed REAL,
        windWaveDirection REAL,
        windWaveHeight REAL,
        windWavePeriod REAL,
        FOREIGN KEY (beach_id) REFERENCES beach_table(beach_id) ON DELETE CASCADE
       ); 
       '''

cur.execute(create_table_query)
conn.commit()

# INSERT SEA_WATER_QUALITY_TABLE:

In [47]:
# %%time
# Wall time: 12min 51s
import psycopg2 as ps

# define credentials 
credentials = {'POSTGRES_ADDRESS' : 'test-surfers-bible-instance.cljoljhkgpfb.ap-southeast-2.rds.amazonaws.com', # change to your endpoint
               'POSTGRES_PORT' : 5432, # change to your port
               'POSTGRES_USERNAME' : '', # change to your username
               'POSTGRES_PASSWORD' : '', # change to your password
               'POSTGRES_DBNAME' : 'test_surfers_bible_db'} # change to your db name

# create connection and cursor    
conn = ps.connect(host=credentials['POSTGRES_ADDRESS'],
                  database=credentials['POSTGRES_DBNAME'],
                  user=credentials['POSTGRES_USERNAME'],
                  password=credentials['POSTGRES_PASSWORD'],
                  port=credentials['POSTGRES_PORT'])

cur = conn.cursor()

fill_question_mark_str = str(tuple(["%s"  for i in swell_df.columns.tolist()])).replace("'", "")
fill_question_mark_str

for row in swell_df.itertuples():
    data_tuple = tuple(row[1:])

    print("data_tuple = ", data_tuple)
    print(" ")
    
    cur.execute("""
                        INSERT INTO SWELL_TABLE
                        (
                            date,
                            beach_id,
                            beach_name,
                            beach_latitude,
                            beach_longitude,
                            beach_state,
                            beach_municipality,
                            airTemperature,
                            cloudCover,
                            currentDirection,
                            currentSpeed,
                            gust,
                            humidity,
                            precipitation,
                            pressure,
                            seaLevel,
                            secondarySwellDirection,
                            secondarySwellHeight,
                            secondarySwellPeriod,
                            swellDirection,
                            swellHeight,
                            swellPeriod,
                            time,
                            visibility,
                            waterTemperature,
                            waveDirection,
                            waveHeight,
                            wavePeriod,
                            windDirection,
                            windSpeed,
                            windWaveDirection,
                            windWaveHeight,
                            windWavePeriod
                         ) VALUES  
                         """ + fill_question_mark_str + " ;"
                , data_tuple)    

conn.commit()
cur.close()
conn.close()

data_tuple =  ('2020-06-05', 1, 'ADDISCOT BEACH', -38.3823, 144.257, 'VIC', 'SURF COAST SHIRE', 10.15, 100.0, 243.43, 0.03, 4.91, 73.4, 0.0, 1030.2, 0.3, 247.87, 0.33, 4.31, 200.78, 0.87, 11.24, '2020-06-05T10:00:00', 24.13, 13.65, 201.79, 0.88, 11.03, 320.09, 3.82, 320.2, 0.13, 1.83)
 
data_tuple =  ('2020-06-05', 1, 'ADDISCOT BEACH', -38.3823, 144.257, 'VIC', 'SURF COAST SHIRE', 10.57, 98.33, 242.65, 0.03, 4.53, 71.2, 0.0, 1029.65, 0.3, 247.87, 0.33, 4.31, 201.38, 0.86, 11.17, '2020-06-05T11:00:00', 24.13, 13.62, 203.49, 0.88, 10.81, 315.74, 4.27, 317.01, 0.16, 1.92)
 
data_tuple =  ('2020-06-05', 1, 'ADDISCOT BEACH', -38.3823, 144.257, 'VIC', 'SURF COAST SHIRE', 10.99, 96.67, 242.65, 0.03, 4.15, 69.0, 0.0, 1029.1, 0.3, 247.87, 0.33, 4.31, 201.98, 0.84, 11.09, '2020-06-05T12:00:00', 24.14, 13.59, 205.19, 0.87, 10.59, 311.38, 4.72, 313.82, 0.2, 2.0)
 
data_tuple =  ('2020-06-05', 1, 'ADDISCOT BEACH', -38.3823, 144.257, 'VIC', 'SURF COAST SHIRE', 11.41, 95.0, 242.65, 0.03, 3.77, 66.8, 

data_tuple =  ('2020-06-05', 1, 'ADDISCOT BEACH', -38.3823, 144.257, 'VIC', 'SURF COAST SHIRE', 10.59, 87.0, 54.46, 0.01, 7.64, 67.1, 0.02, 1026.45, 0.22, 238.31, 0.52, 16.08, 182.83, 1.16, 9.54, '2020-06-06T20:00:00', 24.14, 13.66, 186.26, 1.35, 7.93, 199.32, 6.78, 195.22, 0.7, 3.49)
 
data_tuple =  ('2020-06-05', 1, 'ADDISCOT BEACH', -38.3823, 144.257, 'VIC', 'SURF COAST SHIRE', 10.54, 93.5, 54.46, 0.01, 7.74, 67.3, 0.05, 1026.61, 0.22, 239.17, 0.47, 16.2, 183.11, 1.16, 9.46, '2020-06-06T21:00:00', 24.14, 13.67, 185.89, 1.35, 7.93, 197.01, 6.75, 193.54, 0.68, 3.47)
 
data_tuple =  ('2020-06-05', 1, 'ADDISCOT BEACH', -38.3823, 144.257, 'VIC', 'SURF COAST SHIRE', 10.48, 100.0, 54.46, 0.01, 7.85, 67.5, 0.07, 1026.76, 0.22, 240.02, 0.43, 16.32, 183.39, 1.17, 9.37, '2020-06-06T22:00:00', 24.14, 13.68, 185.53, 1.35, 7.92, 194.7, 6.73, 191.87, 0.67, 3.44)
 
data_tuple =  ('2020-06-05', 1, 'ADDISCOT BEACH', -38.3823, 144.257, 'VIC', 'SURF COAST SHIRE', 10.47, 99.83, 54.46, 0.01, 7.92, 67.8, 

data_tuple =  ('2020-06-05', 2, 'APEX BEACH', -35.813, 145.547, 'VIC', 'MOIRA SHIRE', 4.12, 64.83, nan, nan, 1.35, 90.47, 0.0, 1027.53, nan, nan, nan, nan, nan, nan, nan, '2020-06-06T03:00:00', 24.13, 2.35, 216.07, 0.35, 8.71, 135.84, 1.05, nan, nan, nan)
 
data_tuple =  ('2020-06-05', 2, 'APEX BEACH', -35.813, 145.547, 'VIC', 'MOIRA SHIRE', 3.81, 75.0, nan, nan, 1.2, 91.0, 0.0, 1027.23, nan, nan, nan, nan, nan, nan, nan, '2020-06-06T04:00:00', 24.13, 2.05, 216.07, 0.35, 8.72, 136.83, 0.94, nan, nan, nan)
 
data_tuple =  ('2020-06-05', 2, 'APEX BEACH', -35.813, 145.547, 'VIC', 'MOIRA SHIRE', 3.68, 78.67, nan, nan, 1.16, 91.33, 0.0, 1027.41, nan, nan, nan, nan, nan, nan, nan, '2020-06-06T05:00:00', 24.13, 1.92, 216.15, 0.35, 8.7, 128.71, 0.91, nan, nan, nan)
 
data_tuple =  ('2020-06-05', 2, 'APEX BEACH', -35.813, 145.547, 'VIC', 'MOIRA SHIRE', 3.54, 82.33, nan, nan, 1.13, 91.67, 0.0, 1027.58, nan, nan, nan, nan, nan, nan, nan, '2020-06-06T06:00:00', 24.13, 1.79, 216.15, 0.35, 8.74, 120

data_tuple =  ('2020-06-05', 3, 'BACK BEACH', -38.5269, 145.37, 'VIC', 'BASS COAST SHIRE', 10.05, 100.0, 297.03, 0.11, 7.11, 73.4, 0.0, 1029.92, 0.32, 239.55, 0.19, 4.74, 214.81, 0.96, 11.07, '2020-06-05T10:00:00', 24.13, 11.75, 221.69, 1.02, 10.11, 327.86, 6.29, 320.25, 0.34, 2.62)
 
data_tuple =  ('2020-06-05', 3, 'BACK BEACH', -38.5269, 145.37, 'VIC', 'BASS COAST SHIRE', 10.4, 99.33, 297.22, 0.12, 6.43, 71.77, 0.0, 1029.35, 0.32, 239.55, 0.19, 4.74, 215.56, 0.95, 10.92, '2020-06-05T11:00:00', 24.13, 12.05, 225.82, 1.04, 9.67, 320.79, 6.49, 314.95, 0.4, 2.77)
 
data_tuple =  ('2020-06-05', 3, 'BACK BEACH', -38.5269, 145.37, 'VIC', 'BASS COAST SHIRE', 10.75, 98.67, 297.38, 0.13, 5.75, 70.13, 0.0, 1028.77, 0.32, 239.55, 0.19, 4.74, 216.3, 0.95, 10.76, '2020-06-05T12:00:00', 24.14, 12.36, 229.94, 1.06, 9.24, 313.72, 6.69, 309.64, 0.47, 2.92)
 
data_tuple =  ('2020-06-05', 3, 'BACK BEACH', -38.5269, 145.37, 'VIC', 'BASS COAST SHIRE', 11.11, 98.0, 297.34, 0.13, 5.07, 68.5, 0.0, 1028.19, 0

data_tuple =  ('2020-06-05', 3, 'BACK BEACH', -38.5269, 145.37, 'VIC', 'BASS COAST SHIRE', 9.65, 98.5, 120.63, 0.09, 5.73, 66.3, 0.0, 1025.32, 0.21, 229.89, 0.92, 14.54, 198.0, 1.21, 10.29, '2020-06-06T19:00:00', 24.14, 11.25, 201.3, 1.58, 7.9, 211.23, 8.48, 205.75, 1.01, 4.52)
 
data_tuple =  ('2020-06-05', 3, 'BACK BEACH', -38.5269, 145.37, 'VIC', 'BASS COAST SHIRE', 9.52, 99.0, 120.63, 0.09, 5.94, 67.33, 0.02, 1025.48, 0.21, 229.78, 0.92, 14.47, 198.08, 1.22, 10.22, '2020-06-06T20:00:00', 24.14, 11.22, 200.39, 1.61, 7.79, 208.04, 8.56, 203.47, 1.06, 4.58)
 
data_tuple =  ('2020-06-05', 3, 'BACK BEACH', -38.5269, 145.37, 'VIC', 'BASS COAST SHIRE', 9.4, 99.5, 120.07, 0.09, 6.14, 68.37, 0.05, 1025.65, 0.21, 229.68, 0.91, 14.41, 198.15, 1.22, 10.14, '2020-06-06T21:00:00', 24.14, 11.2, 199.47, 1.65, 7.67, 204.85, 8.63, 201.19, 1.1, 4.65)
 
data_tuple =  ('2020-06-05', 3, 'BACK BEACH', -38.5269, 145.37, 'VIC', 'BASS COAST SHIRE', 9.28, 100.0, 119.5, 0.09, 6.35, 69.4, 0.07, 1025.82, 0.21, 

...

data_tuple =  ('2020-06-05', 197, 'WRECK BEACH', -38.7546, 143.212, 'VIC', 'CORANGAMITE SHIRE', 10.2, 100.0, 153.43, 0.02, 7.75, 68.03, 0.0, 1027.33, 0.22, 226.83, 0.67, 17.56, 221.1, 2.44, 11.94, '2020-06-07T02:00:00', 24.13, 14.12, 218.78, 2.54, 11.35, 186.07, 7.18, 186.74, 0.67, 3.69)
 
data_tuple =  ('2020-06-05', 197, 'WRECK BEACH', -38.7546, 143.212, 'VIC', 'CORANGAMITE SHIRE', 10.26, 100.0, 153.43, 0.02, 8.02, 68.17, 0.0, 1027.05, 0.22, 226.76, 0.64, 17.51, 221.26, 2.44, 11.91, '2020-06-07T03:00:00', 24.13, 14.09, 218.75, 2.54, 11.27, 186.42, 7.34, 187.59, 0.71, 3.76)
 
data_tuple =  ('2020-06-05', 197, 'WRECK BEACH', -38.7546, 143.212, 'VIC', 'CORANGAMITE SHIRE', 10.31, 100.0, 152.24, 0.02, 8.3, 68.3, 0.0, 1026.78, 0.22, 226.69, 0.61, 17.45, 221.43, 2.43, 11.88, '2020-06-07T04:00:00', 24.13, 14.06, 218.72, 2.54, 11.19, 186.78, 7.49, 188.44, 0.74, 3.84)
 
data_tuple =  ('2020-06-05', 197, 'WRECK BEACH', -38.7546, 143.212, 'VIC', 'CORANGAMITE SHIRE', 10.56, 100.0, 152.24, 0.02, 8

data_tuple =  ('2020-06-05', 198, 'YANAKIE BEACH', -38.8108, 146.269, 'VIC', 'SOUTH GIPPSLAND SHIRE', 10.65, 38.0, 75.89, 0.18, 3.95, 83.8, 0.0, 1025.25, 0.26, 222.84, 0.4, 15.04, 221.78, 0.54, 11.56, '2020-06-06T10:00:00', 24.14, 12.05, 223.9, 0.55, 11.14, 294.16, 4.3, 294.27, 0.11, 1.9)
 
data_tuple =  ('2020-06-05', 198, 'YANAKIE BEACH', -38.8108, 146.269, 'VIC', 'SOUTH GIPPSLAND SHIRE', 10.76, 37.0, 73.59, 0.17, 5.25, 78.7, 0.0, 1024.73, 0.24, 222.45, 0.4, 15.4, 221.05, 0.55, 11.44, '2020-06-06T11:00:00', 24.14, 12.24, 224.76, 0.57, 10.77, 294.09, 4.85, 291.74, 0.15, 2.02)
 
data_tuple =  ('2020-06-05', 198, 'YANAKIE BEACH', -38.8108, 146.269, 'VIC', 'SOUTH GIPPSLAND SHIRE', 10.87, 36.0, 71.57, 0.15, 6.54, 73.6, 0.0, 1024.22, 0.22, 222.07, 0.39, 15.75, 220.33, 0.55, 11.33, '2020-06-06T12:00:00', 24.13, 12.42, 225.62, 0.58, 10.4, 294.01, 5.4, 289.22, 0.18, 2.15)
 
data_tuple =  ('2020-06-05', 198, 'YANAKIE BEACH', -38.8108, 146.269, 'VIC', 'SOUTH GIPPSLAND SHIRE', 10.98, 35.0, 68.68

data_tuple =  ('2020-06-05', 199, 'ZINETTIS BEACH NO. 1', -35.967, 145.941, 'VIC', 'MOIRA SHIRE', 11.95, 0.0, nan, nan, 1.94, 67.2, 0.0, 1027.35, nan, nan, nan, nan, nan, nan, nan, '2020-06-05T16:00:00', 24.13, 12.05, 217.9, 0.33, 8.78, 238.08, 1.34, nan, nan, nan)
 
data_tuple =  ('2020-06-05', 199, 'ZINETTIS BEACH NO. 1', -35.967, 145.941, 'VIC', 'MOIRA SHIRE', 10.22, 2.83, nan, nan, 1.95, 72.93, 0.0, 1027.91, nan, nan, nan, nan, nan, nan, nan, '2020-06-05T17:00:00', 24.14, 9.59, 221.13, 0.33, 8.71, 222.35, 1.4, nan, nan, nan)
 
data_tuple =  ('2020-06-05', 199, 'ZINETTIS BEACH NO. 1', -35.967, 145.941, 'VIC', 'MOIRA SHIRE', 8.48, 5.67, nan, nan, 1.95, 78.67, 0.0, 1028.47, nan, nan, nan, nan, nan, nan, nan, '2020-06-05T18:00:00', 24.14, 7.13, 220.08, 0.35, 8.75, 206.63, 1.46, nan, nan, nan)
 
data_tuple =  ('2020-06-05', 199, 'ZINETTIS BEACH NO. 1', -35.967, 145.941, 'VIC', 'MOIRA SHIRE', 6.75, 8.5, nan, nan, 1.95, 84.4, 0.0, 1029.03, nan, nan, nan, nan, nan, nan, nan, '2020-06-05T19

data_tuple =  ('2020-06-05', 199, 'ZINETTIS BEACH NO. 1', -35.967, 145.941, 'VIC', 'MOIRA SHIRE', 2.79, 0.0, nan, nan, 7.55, 91.83, 0.0, 1025.41, nan, nan, nan, nan, nan, nan, nan, '2020-06-07T05:00:00', 24.13, 1.91, 211.26, 0.37, 6.65, 214.32, 3.44, nan, nan, nan)
 
data_tuple =  ('2020-06-05', 199, 'ZINETTIS BEACH NO. 1', -35.967, 145.941, 'VIC', 'MOIRA SHIRE', 2.37, 0.0, nan, nan, 7.0, 92.07, 0.0, 1025.93, nan, nan, nan, nan, nan, nan, nan, '2020-06-07T06:00:00', 24.14, 1.46, 212.99, 0.37, 6.65, 213.46, 3.32, nan, nan, nan)
 
data_tuple =  ('2020-06-05', 199, 'ZINETTIS BEACH NO. 1', -35.967, 145.941, 'VIC', 'MOIRA SHIRE', 1.95, 0.0, nan, nan, 6.45, 92.3, 0.0, 1026.44, nan, nan, nan, nan, nan, nan, nan, '2020-06-07T07:00:00', 24.14, 1.01, 221.89, 0.36, 6.09, 212.59, 3.2, nan, nan, nan)
 
data_tuple =  ('2020-06-05', 199, 'ZINETTIS BEACH NO. 1', -35.967, 145.941, 'VIC', 'MOIRA SHIRE', 3.77, 0.0, nan, nan, 6.86, 83.93, 0.0, 1026.59, nan, nan, nan, nan, nan, nan, nan, '2020-06-07T08:00:

data_tuple =  ('2020-06-05', 200, 'ZINETTIS BEACH NO. 2', -35.97, 145.936, 'VIC', 'MOIRA SHIRE', 11.18, 91.0, nan, nan, 1.74, 64.8, 0.0, 1025.32, nan, nan, nan, nan, nan, nan, nan, '2020-06-06T13:00:00', 24.13, 15.51, 212.76, 0.37, 9.23, 267.48, 1.18, nan, nan, nan)
 
data_tuple =  ('2020-06-05', 200, 'ZINETTIS BEACH NO. 2', -35.97, 145.936, 'VIC', 'MOIRA SHIRE', 10.97, 94.0, nan, nan, 2.21, 66.57, 0.0, 1025.04, nan, nan, nan, nan, nan, nan, nan, '2020-06-06T14:00:00', 24.13, 13.83, 212.8, 0.37, 9.28, 260.71, 1.49, nan, nan, nan)
 
data_tuple =  ('2020-06-05', 200, 'ZINETTIS BEACH NO. 2', -35.97, 145.936, 'VIC', 'MOIRA SHIRE', 10.76, 97.0, nan, nan, 2.69, 68.33, 0.0, 1024.76, nan, nan, nan, nan, nan, nan, nan, '2020-06-06T15:00:00', 24.13, 12.16, 211.49, 0.36, 9.54, 253.94, 1.8, nan, nan, nan)
 
data_tuple =  ('2020-06-05', 200, 'ZINETTIS BEACH NO. 2', -35.97, 145.936, 'VIC', 'MOIRA SHIRE', 10.55, 100.0, nan, nan, 3.16, 70.1, 0.0, 1024.47, nan, nan, nan, nan, nan, nan, nan, '2020-06-06

# ASTRONOMICAL DATA:

# astronomy: API CALLS:

In [54]:
astronomy_col_lst = [
    'date',
    'beach_id',
    'beach_name',
    'beach_latitude',
    'beach_longitude',
    'beach_state',    
    "beach_municipality",
    
    'astronomicalDawn',
     'astronomicalDusk',
     'civilDawn',
     'civilDusk',
     'moonFraction',
     'moonPhase',
     'moonrise',
     'moonset',
     'nauticalDawn',
     'nauticalDusk',
     'sunrise',
     'sunset',
     'time'
]
astronomy_df = pd.DataFrame(columns = astronomy_col_lst
                         )
astronomy_df

Empty DataFrame
Columns: [date, beach_id, beach_name, beach_latitude, beach_longitude, beach_state, beach_municipality, astronomicalDawn, astronomicalDusk, civilDawn, civilDusk, moonFraction, moonPhase, moonrise, moonset, nauticalDawn, nauticalDusk, sunrise, sunset, time]
Index: []

## Convert API response JSON dict to DF row:

In [56]:
# %%time
# Wall time: 4min 34s
import datetime
for api_limit, api_no in zip(range(0,200,50) ,range(9,13)):
    
    print("++++++++++++++++++++++++++++++++++++++++++++")
    API_KEY = SG_API_KEY_DICT[str(api_no)]
    print("ASTRONOMY: api_limit = ", api_limit)
    print("api_no = ", api_no)
    print("++++++++++++++++++++++++++++++++++++++++++++")
    
    for index, row in beach_df.loc[api_limit  : api_limit + 50,].iterrows():

        print("")
        print("index = ", index)
        print("beach_name", row["beach_name"])
        print(" ")

        latitude = row['beach_latitude']
        longitude = row['beach_longitude']

        start_date = given_date
        end_date = str((datetime.datetime.strptime(given_date, "%Y-%m-%d") + datetime.timedelta(days = 1)).date())
#         end_date = '2020-06-07'

        url_str = "https://api.stormglass.io/v2/astronomy/point?"
        url_str += "lat="+ str(latitude) +"&"
        url_str += "lng="+str(longitude) + "&"
        url_str += "start=" + start_date + "&"
        url_str += "end="+ end_date 
    #         + "&"
    #         url_str += "params=waterTemperature,wavePeriod,waveDirection,waveHeight,windWaveDirection,windWaveHeight,windWavePeriod,astronomyPeriod,secondaryastronomyPeriod,astronomyDirection,secondaryastronomyDirection,astronomyHeight,secondaryastronomyHeight,windSpeed,windDirection,airTemperature,precipitation,gust,cloudCover,humidity,pressure,visibility,currentSpeed,currentDirection,seaLevel"

        payload = {}
        headers = {
          'Authorization': API_KEY
        }
        try:
            response = requests.request("GET", url_str, headers=headers, data = payload)
            response_dict = json.loads(response.text)    
        #     print("response_dict = ", response_dict)
            astronomy_dict = {}

            for hour_dict in response_dict['data']:
        #         print("hour_dict = ", hour_dict)

                astronomy_dict['date'] = given_date

                for beach_col in beach_df.columns.tolist():
                    astronomy_dict[beach_col] = row[beach_col]     

                astronomy_col_lst = list(hour_dict.keys())
        #             astronomy_col_lst.remove("time")

                for astronomy_col in astronomy_col_lst:

                    astronomy_dict[astronomy_col] = hour_dict[astronomy_col]

        #             astronomy_dict['time'] = hour_dict['time']

                astronomy_df = astronomy_df.append(astronomy_dict, ignore_index=True)
        except:
            print("++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++")
            print("FAILED REQUEST!!!!!!!!!!!!!!!!!!!!!!!!!!!!!")
            print("api_limit = ", api_limit)
            print("api_no = ", api_no)
            print("index = ", index)
            print("beach_name", row["beach_name"])            
            print("++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++")
###################################################################################################################


++++++++++++++++++++++++++++++++++++++++++++
ASTRONOMY: api_limit =  0
api_no =  9
++++++++++++++++++++++++++++++++++++++++++++

index =  0
beach_name ADDISCOT BEACH
 

index =  1
beach_name APEX BEACH
 

index =  2
beach_name BACK BEACH
 

index =  3
beach_name BANCOORA BEACH
 

index =  4
beach_name BARRY BEACH
 

index =  5
beach_name BARRYS BEACH
 

index =  6
beach_name BAY BEACH
 

index =  7
beach_name BELL BEACH
 

index =  8
beach_name BELLS BEACH
 

index =  9
beach_name BERRY BEACH
 

index =  10
beach_name BETKA BEACH
 

index =  11
beach_name BIDDLES BEACH
 

index =  12
beach_name BIRDROCK BEACH
 

index =  13
beach_name BIRRELLS BEACH
 

index =  14
beach_name BLACK BEACH
 

index =  15
beach_name BOOMANGONG BEACH
 

index =  16
beach_name BOUCHIERS BEACH
 

index =  17
beach_name BOURKES BEACH NO. 1
 

index =  18
beach_name BOURKES BEACH NO. 2
 

index =  19
beach_name BOURKES BEACH NO. 3
 

index =  20
beach_name BREENS BEACH
 

index =  21
beach_name BRENTNALLS BEACH


index =  181
beach_name TOORA BEACH
 

index =  182
beach_name TRUES BEACH
 

index =  183
beach_name TURRAS BEACH
 

index =  184
beach_name ULUPNA BEACH
 

index =  185
beach_name WEISS BEACH
 

index =  186
beach_name WESTERN BEACH
 

index =  187
beach_name WESTERN PARK BEACH
 

index =  188
beach_name WHITES BEACH
 

index =  189
beach_name WILD DOG BEACH
 

index =  190
beach_name WILD DOG SHORE
 

index =  191
beach_name WILLOW BEACH
 

index =  192
beach_name WILSONS BEACH
 

index =  193
beach_name WOODSIDE BEACH
 

index =  194
beach_name WOOLAMAI SURF BEACH
 

index =  195
beach_name WOOLLEY BEACH
 

index =  196
beach_name WRECK BEACH
 

index =  197
beach_name YANAKIE BEACH
 

index =  198
beach_name ZINETTIS BEACH NO. 1
 

index =  199
beach_name ZINETTIS BEACH NO. 2
 


# CONVERT UTC TIME TO AUSTRALIA TIME:

In [57]:
def convert_datetime_in_dif_timezones(from_datetime_str, from_timezone_str, to_timezone_str, 
                                      datetime_format = '%Y-%m-%dT%H:%M:%S'):
#     USE pytz.all_timezones to get all timestamps
    from datetime import datetime
    import pytz
    try:
        date_time_obj = datetime.strptime(from_datetime_str, datetime_format)
    #     print("date_time_obj = ", date_time_obj)

        old_timezone = pytz.timezone(from_timezone_str)
        new_timezone = pytz.timezone(to_timezone_str)

        new_timezone_timestamp = old_timezone.localize(date_time_obj).astimezone(new_timezone).strftime("%Y-%m-%dT%H:%M:%S") 
    #     print("new_timezone_timestamp", new_timezone_timestamp)
        return str(new_timezone_timestamp)
    except:
        print("from_datetime_str",  from_datetime_str)

In [58]:
time_col_lst = ['astronomicalDawn', 'astronomicalDusk', 'civilDawn', 'civilDusk', 'moonrise', 'moonset',
                'nauticalDawn', 'nauticalDusk', 'sunrise', 'sunset', 'time']

for time_col in time_col_lst: 
    astronomy_df[time_col] = astronomy_df[time_col].apply(lambda x: convert_datetime_in_dif_timezones(
                                                                                from_datetime_str = x, 
                                                                                from_timezone_str = 'UTC', 
                                                                                to_timezone_str ='Australia/Melbourne', 
                                                                                datetime_format = '%Y-%m-%dT%H:%M:%S+00:00'))

from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_datetime_str None
from_dateti

In [59]:
astronomy_df.drop("moonPhase", axis=1, inplace = True)

# CREATE astronomy_TABLE:

In [60]:
import psycopg2 as ps

# define credentials 
credentials = {'POSTGRES_ADDRESS' : 'test-surfers-bible-instance.cljoljhkgpfb.ap-southeast-2.rds.amazonaws.com', # change to your endpoint
               'POSTGRES_PORT' : 5432, # change to your port
               'POSTGRES_USERNAME' : '', # change to your username
               'POSTGRES_PASSWORD' : '', # change to your password
               'POSTGRES_DBNAME' : 'test_surfers_bible_db'} # change to your db name

# create connection and cursor    
conn = ps.connect(host=credentials['POSTGRES_ADDRESS'],
                  database=credentials['POSTGRES_DBNAME'],
                  user=credentials['POSTGRES_USERNAME'],
                  password=credentials['POSTGRES_PASSWORD'],
                  port=credentials['POSTGRES_PORT'])

cur = conn.cursor()

# cur.execute("DROP TABLE SEA_WATER_QUALITY_TABLE;")

create_table_query = '''
      CREATE TABLE IF NOT EXISTS astronomy_TABLE
      (
        astronomy_id SERIAL PRIMARY KEY,
        date DATE,
        beach_id INTEGER,
        beach_name TEXT,
        beach_latitude REAL,
        beach_longitude REAL,
        beach_state TEXT,
        beach_municipality TEXT,
        astronomicalDawn TEXT,
        astronomicalDusk TEXT,
        civilDawn TEXT,
        civilDusk TEXT,
        moonFraction REAL,
        moonrise TEXT,
        moonset TEXT,
        nauticalDawn TEXT,
        nauticalDusk TEXT,
        sunrise TEXT,
        sunset TEXT,
        time TEXT,
        FOREIGN KEY (beach_id) REFERENCES beach_table(beach_id) ON DELETE CASCADE
       ); 
       '''

cur.execute(create_table_query)
conn.commit()

# INSERT astronomy_TABLE:

In [61]:
# %%time
# Wall time: 12min 51s
import psycopg2 as ps

# define credentials 
credentials = {'POSTGRES_ADDRESS' : 'test-surfers-bible-instance.cljoljhkgpfb.ap-southeast-2.rds.amazonaws.com', # change to your endpoint
               'POSTGRES_PORT' : 5432, # change to your port
               'POSTGRES_USERNAME' : '', # change to your username
               'POSTGRES_PASSWORD' : '', # change to your password
               'POSTGRES_DBNAME' : 'test_surfers_bible_db'} # change to your db name

# create connection and cursor    
conn = ps.connect(host=credentials['POSTGRES_ADDRESS'],
                  database=credentials['POSTGRES_DBNAME'],
                  user=credentials['POSTGRES_USERNAME'],
                  password=credentials['POSTGRES_PASSWORD'],
                  port=credentials['POSTGRES_PORT'])

cur = conn.cursor()

fill_question_mark_str = str(tuple(["%s"  for i in astronomy_df.columns.tolist()])).replace("'", "")
fill_question_mark_str

for row in astronomy_df.itertuples():
    data_tuple = tuple(row[1:])

    print("data_tuple = ", data_tuple)
    print(" ")
    
    cur.execute("""
                        INSERT INTO astronomy_TABLE
                        (
                            date,
                            beach_id,
                            beach_name,
                            beach_latitude,
                            beach_longitude,
                            beach_state,
                            beach_municipality,
                            astronomicalDawn,
                            astronomicalDusk,
                            civilDawn,
                            civilDusk,
                            moonFraction,
                            moonrise,
                            moonset,
                            nauticalDawn,
                            nauticalDusk,
                            sunrise,
                            sunset,
                            time
                         ) VALUES  
                         """ + fill_question_mark_str + " ;"
                , data_tuple)    

conn.commit()
cur.close()
conn.close()

data_tuple =  ('2020-06-05', 1, 'ADDISCOT BEACH', -38.3823, 144.257, 'VIC', 'SURF COAST SHIRE', '2020-06-05T06:00:24', '2020-06-05T18:45:23', '2020-06-05T07:05:25', '2020-06-05T17:40:23', 0.9932816019731637, '2020-06-05T16:54:20', '2020-06-06T08:26:54', '2020-06-05T06:32:27', '2020-06-05T18:13:21', '2020-06-05T07:34:50', '2020-06-05T17:10:57', '2020-06-05T10:00:00')
 
data_tuple =  ('2020-06-05', 1, 'ADDISCOT BEACH', -38.3823, 144.257, 'VIC', 'SURF COAST SHIRE', '2020-06-06T06:00:54', '2020-06-06T18:45:14', '2020-06-06T07:05:58', '2020-06-06T17:40:10', 0.9986437936619488, '2020-06-07T08:59:24', '2020-06-07T08:19:44', '2020-06-06T06:32:58', '2020-06-06T18:13:10', '2020-06-06T07:35:25', '2020-06-06T17:10:43', '2020-06-06T10:00:00')
 
data_tuple =  ('2020-06-05', 1, 'ADDISCOT BEACH', -38.3823, 144.257, 'VIC', 'SURF COAST SHIRE', '2020-06-07T06:01:22', '2020-06-07T18:45:07', '2020-06-07T07:06:29', '2020-06-07T17:40:00', 0.9787763816926336, '2020-06-07T18:49:57', '2020-06-07T10:36:41', '202

data_tuple =  ('2020-06-05', 9, 'BELLS BEACH', -38.3688, 144.283, 'VIC', 'SURF COAST SHIRE', '2020-06-06T06:00:46', '2020-06-06T18:45:09', '2020-06-06T07:05:50', '2020-06-06T17:40:06', 0.9986437936619488, '2020-06-07T08:59:19', '2020-06-07T08:22:31', '2020-06-06T06:32:50', '2020-06-06T18:13:06', '2020-06-06T07:35:16', '2020-06-06T17:10:39', '2020-06-06T10:00:00')
 
data_tuple =  ('2020-06-05', 9, 'BELLS BEACH', -38.3688, 144.283, 'VIC', 'SURF COAST SHIRE', '2020-06-07T06:01:15', '2020-06-07T18:45:02', '2020-06-07T07:06:21', '2020-06-07T17:39:55', 0.9787763816926336, '2020-06-07T18:50:02', '2020-06-07T10:34:34', '2020-06-07T06:33:20', '2020-06-07T18:12:57', '2020-06-07T07:35:50', '2020-06-07T17:10:26', '2020-06-07T10:00:00')
 
data_tuple =  ('2020-06-05', 10, 'BERRY BEACH', -38.5176, 145.203, 'VIC', 'BASS COAST SHIRE', '2020-06-05T05:56:48', '2020-06-05T18:41:25', '2020-06-05T07:01:56', '2020-06-05T17:36:17', 0.9932816019731637, '2020-06-05T16:51:35', '2020-06-06T08:03:07', '2020-06-05T

data_tuple =  ('2020-06-05', 17, 'BOUCHIERS BEACH', -35.8383, 145.574, 'VIC', 'MOIRA SHIRE', '2020-06-07T05:52:36', '2020-06-07T18:43:21', '2020-06-07T06:55:31', '2020-06-07T17:40:26', 0.9787763816926336, '2020-06-07T18:46:15', None, '2020-06-07T06:23:39', '2020-06-07T18:12:18', '2020-06-07T07:23:50', '2020-06-07T17:12:07', '2020-06-07T10:00:00')
 
data_tuple =  ('2020-06-05', 18, 'BOURKES BEACH NO. 1', -35.9768, 145.835, 'VIC', 'MOIRA SHIRE', '2020-06-05T05:50:50', '2020-06-05T18:42:19', '2020-06-05T06:53:46', '2020-06-05T17:39:24', 0.9932816019731637, '2020-06-05T16:54:27', '2020-06-06T08:22:13', '2020-06-05T06:21:54', '2020-06-05T18:11:16', '2020-06-05T07:22:05', '2020-06-05T17:11:05', '2020-06-05T10:00:00')
 
data_tuple =  ('2020-06-05', 18, 'BOURKES BEACH NO. 1', -35.9768, 145.835, 'VIC', 'MOIRA SHIRE', '2020-06-06T05:51:18', '2020-06-06T18:42:12', '2020-06-06T06:54:16', '2020-06-06T17:39:14', 0.9986437936619488, '2020-06-06T17:52:38', '2020-06-07T09:13:25', '2020-06-06T06:22:23',

data_tuple =  ('2020-06-05', 26, 'BURGES BEACH', -37.428, 149.714, 'VIC', 'EAST GIPPSLAND SHIRE', '2020-06-05T05:37:16', '2020-06-05T18:24:51', '2020-06-05T06:41:25', '2020-06-05T17:20:42', 0.9932816019731637, '2020-06-05T16:46:06', '2020-06-06T07:13:37', '2020-06-05T06:08:55', '2020-06-05T17:53:13', '2020-06-05T07:10:23', '2020-06-05T16:51:45', '2020-06-05T10:00:00')
 
data_tuple =  ('2020-06-05', 26, 'BURGES BEACH', -37.428, 149.714, 'VIC', 'EAST GIPPSLAND SHIRE', '2020-06-06T05:37:45', '2020-06-06T18:24:43', '2020-06-06T06:41:57', '2020-06-06T17:20:31', 0.9986437936619488, '2020-06-06T16:46:48', '2020-06-07T08:03:52', '2020-06-06T06:09:25', '2020-06-06T17:53:03', '2020-06-06T07:10:57', '2020-06-06T16:51:31', '2020-06-06T10:00:00')
 
data_tuple =  ('2020-06-05', 26, 'BURGES BEACH', -37.428, 149.714, 'VIC', 'EAST GIPPSLAND SHIRE', '2020-06-07T05:38:13', '2020-06-07T18:24:36', '2020-06-07T06:42:28', '2020-06-07T17:20:21', 0.9787763816926336, '2020-06-07T17:56:45', '2020-06-08T09:12:16'

data_tuple =  ('2020-06-05', 34, 'CLIFTON BEACH', -38.6782, 143.125, 'VIC', 'CORANGAMITE SHIRE', '2020-06-07T06:06:19', '2020-06-07T18:49:14', '2020-06-07T07:11:42', '2020-06-07T17:43:50', 0.9787763816926336, '2020-06-07T18:47:29', None, '2020-06-07T06:38:32', '2020-06-07T18:17:01', '2020-06-07T07:41:21', '2020-06-07T17:14:12', '2020-06-07T10:00:00')
 
data_tuple =  ('2020-06-05', 35, 'COBRAWONGA BEACH NO. 1', -35.9729, 145.792, 'VIC', 'MOIRA SHIRE', '2020-06-05T05:51:00', '2020-06-05T18:42:30', '2020-06-05T06:53:55', '2020-06-05T17:39:35', 0.9932816019731637, '2020-06-05T16:54:35', '2020-06-06T08:21:28', '2020-06-05T06:22:04', '2020-06-05T18:11:27', '2020-06-05T07:22:14', '2020-06-05T17:11:16', '2020-06-05T10:00:00')
 
data_tuple =  ('2020-06-05', 35, 'COBRAWONGA BEACH NO. 1', -35.9729, 145.792, 'VIC', 'MOIRA SHIRE', '2020-06-06T05:51:28', '2020-06-06T18:42:23', '2020-06-06T06:54:26', '2020-06-06T17:39:25', 0.9986437936619488, '2020-06-06T17:52:41', '2020-06-07T09:12:50', '2020-06-06T

...

data_tuple =  ('2020-06-05', 164, 'SOUTHCOMBE BEACH', -38.3922, 142.231, 'VIC', 'MOYNE SHIRE', '2020-06-05T06:08:31', '2020-06-05T18:53:29', '2020-06-05T07:13:32', '2020-06-05T17:48:27', 0.9932816019731637, '2020-06-05T17:49:02', '2020-06-05T17:00:45', '2020-06-05T06:40:34', '2020-06-05T18:21:26', '2020-06-05T07:42:58', '2020-06-05T17:19:02', '2020-06-05T10:00:00')
 
data_tuple =  ('2020-06-05', 164, 'SOUTHCOMBE BEACH', -38.3922, 142.231, 'VIC', 'MOYNE SHIRE', '2020-06-06T06:09:01', '2020-06-06T18:53:20', '2020-06-06T07:14:05', '2020-06-06T17:48:15', 0.9986437936619488, '2020-06-06T17:55:18', '2020-06-07T09:03:22', '2020-06-06T06:41:05', '2020-06-06T18:21:15', '2020-06-06T07:43:33', '2020-06-06T17:18:48', '2020-06-06T10:00:00')
 
data_tuple =  ('2020-06-05', 164, 'SOUTHCOMBE BEACH', -38.3922, 142.231, 'VIC', 'MOYNE SHIRE', '2020-06-07T06:09:29', '2020-06-07T18:53:12', '2020-06-07T07:14:37', '2020-06-07T17:48:05', 0.9787763816926336, '2020-06-07T18:47:57', None, '2020-06-07T06:41:35', '

data_tuple =  ('2020-06-05', 172, 'SUTHERLANDS BEACH', -38.7563, 143.361, 'VIC', 'COLAC OTWAY SHIRE', '2020-06-07T06:05:28', '2020-06-07T18:48:11', '2020-06-07T07:10:57', '2020-06-07T17:42:43', 0.9787763816926336, '2020-06-07T18:47:56', None, '2020-06-07T06:37:44', '2020-06-07T18:15:56', '2020-06-07T07:40:37', '2020-06-07T17:13:02', '2020-06-07T10:00:00')
 
data_tuple =  ('2020-06-05', 173, 'TAYLORS BEACH', -38.3902, 142.172, 'VIC', 'MOYNE SHIRE', '2020-06-05T06:08:45', '2020-06-05T18:53:43', '2020-06-05T07:13:46', '2020-06-05T17:48:42', 0.9932816019731637, '2020-06-05T17:44:14', '2020-06-05T17:01:09', '2020-06-05T06:40:48', '2020-06-05T18:21:40', '2020-06-05T07:43:12', '2020-06-05T17:19:16', '2020-06-05T10:00:00')
 
data_tuple =  ('2020-06-05', 173, 'TAYLORS BEACH', -38.3902, 142.172, 'VIC', 'MOYNE SHIRE', '2020-06-06T06:09:15', '2020-06-06T18:53:34', '2020-06-06T07:14:19', '2020-06-06T17:48:30', 0.9986437936619488, '2020-06-06T17:55:24', '2020-06-07T09:03:29', '2020-06-06T06:41:19', 

data_tuple =  ('2020-06-05', 181, 'TIP BEACH', -37.5739, 149.759, 'VIC', 'EAST GIPPSLAND SHIRE', '2020-06-06T05:37:46', '2020-06-06T18:24:20', '2020-06-06T06:42:06', '2020-06-06T17:20:00', 0.9986437936619488, '2020-06-06T16:48:52', '2020-06-07T08:03:26', '2020-06-06T06:09:30', '2020-06-06T17:52:37', '2020-06-06T07:11:10', '2020-06-06T16:50:56', '2020-06-06T10:00:00')
 
data_tuple =  ('2020-06-05', 181, 'TIP BEACH', -37.5739, 149.759, 'VIC', 'EAST GIPPSLAND SHIRE', '2020-06-07T05:38:14', '2020-06-07T18:24:13', '2020-06-07T06:42:37', '2020-06-07T17:19:50', 0.9787763816926336, '2020-06-07T17:53:07', '2020-06-08T09:11:57', '2020-06-07T06:09:59', '2020-06-07T17:52:29', '2020-06-07T07:11:43', '2020-06-07T16:50:45', '2020-06-07T10:00:00')
 
data_tuple =  ('2020-06-05', 182, 'TOORA BEACH', -38.6913, 146.336, 'VIC', 'SOUTH GIPPSLAND SHIRE', '2020-06-05T05:52:30', '2020-06-05T18:36:39', '2020-06-05T06:57:48', '2020-06-05T17:31:21', 0.9932816019731637, '2020-06-05T16:48:35', '2020-06-06T08:07:04'

data_tuple =  ('2020-06-05', 190, 'WILD DOG BEACH', -38.03, 141.14, 'VIC', 'GLENELG SHIRE', '2020-06-05T06:12:24', '2020-06-05T18:58:20', '2020-06-05T07:17:05', '2020-06-05T17:53:39', 0.9932816019731637, '2020-06-05T16:58:34', '2020-06-06T08:00:56', '2020-06-05T06:44:17', '2020-06-05T18:26:26', '2020-06-05T07:46:20', '2020-06-05T17:24:24', '2020-06-05T10:00:00')
 
data_tuple =  ('2020-06-05', 190, 'WILD DOG BEACH', -38.03, 141.14, 'VIC', 'GLENELG SHIRE', '2020-06-06T06:12:53', '2020-06-06T18:58:11', '2020-06-06T07:17:38', '2020-06-06T17:53:27', 0.9986437936619488, '2020-06-06T17:57:23', '2020-06-07T09:05:13', '2020-06-06T06:44:48', '2020-06-06T18:26:16', '2020-06-06T07:46:55', '2020-06-06T17:24:10', '2020-06-06T10:00:00')
 
data_tuple =  ('2020-06-05', 190, 'WILD DOG BEACH', -38.03, 141.14, 'VIC', 'GLENELG SHIRE', '2020-06-07T06:13:21', '2020-06-07T18:58:04', '2020-06-07T07:18:09', '2020-06-07T17:53:16', 0.9787763816926336, '2020-06-07T18:50:31', None, '2020-06-07T06:45:18', '2020-06-0

data_tuple =  ('2020-06-05', 198, 'YANAKIE BEACH', -38.8108, 146.269, 'VIC', 'SOUTH GIPPSLAND SHIRE', '2020-06-06T05:53:26', '2020-06-06T18:36:36', '2020-06-06T06:58:54', '2020-06-06T17:31:08', 0.9986437936619488, '2020-06-06T17:58:52', '2020-06-07T09:01:06', '2020-06-06T06:25:41', '2020-06-06T18:04:21', '2020-06-06T07:28:34', '2020-06-06T17:01:28', '2020-06-06T10:00:00')
 
data_tuple =  ('2020-06-05', 198, 'YANAKIE BEACH', -38.8108, 146.269, 'VIC', 'SOUTH GIPPSLAND SHIRE', '2020-06-07T05:53:55', '2020-06-07T18:36:29', '2020-06-07T06:59:26', '2020-06-07T17:30:57', 0.9787763816926336, '2020-06-07T17:44:37', None, '2020-06-07T06:26:12', '2020-06-07T18:04:12', '2020-06-07T07:29:08', '2020-06-07T17:01:15', '2020-06-07T10:00:00')
 
data_tuple =  ('2020-06-05', 199, 'ZINETTIS BEACH NO. 1', -35.967, 145.941, 'VIC', 'MOIRA SHIRE', '2020-06-05T05:50:24', '2020-06-05T18:41:55', '2020-06-05T06:53:19', '2020-06-05T17:39:00', 0.9932816019731637, '2020-06-05T16:54:08', '2020-06-06T08:24:27', '2020-0

___
___
___


# SEA_WATER_QUALITY DATA:

In [10]:
bio_col_lst = [  
                'date',
                'beach_id',
                'beach_name',
                'beach_latitude',
                'beach_longitude',
                'beach_state',    
                "beach_municipality",
    
                 'chlorophyll',
                 'iron',
                 'nitrate',
                 'oxygen',
                 'ph',
                 'phosphate',
                 'phyto',
                 'phytoplankton',
                 'salinity',
                 'silicate',
                 'time'
                ]

bio_df = pd.DataFrame(columns = bio_col_lst
                         )
# bio_df

# SEA_WATER_QUALITY: API CALLS:

## Convert API response JSON dict to DF row:

In [13]:
# %%time
# Wall time: 5min 34s
import datetime
for api_limit, api_no in zip(range(0,200,50) ,range(1,5)):
    print("++++++++++++++++++++++++++++++++++++++++++++")
    API_KEY = SG_API_KEY_DICT[str(api_no)]
    print("api_limit = ", api_limit)
    print("api_no = ", api_no)
    print("++++++++++++++++++++++++++++++++++++++++++++")
    
    for index, row in beach_df.loc[api_limit  : api_limit + 50,].iterrows():
        print("")
        print("index = ", index)
        print("beach_name", row["beach_name"])
        print(" ")

        latitude = row['beach_latitude']
        longitude = row['beach_longitude']

        start_date = given_date
#         end_date = str((datetime.datetime.strptime(given_date, "%Y-%m-%d") + datetime.timedelta(days = 1)).date())
        end_date = '2020-06-06'


        url_str = "https://api.stormglass.io/v2/bio/point?"
        url_str += "lat="+ str(latitude) +"&"
        url_str += "lng="+str(longitude) + "&"
        url_str += "start=" + start_date + "&"
        url_str += "end="+ end_date + "&"
        url_str += "params=iron,nitrate,chlorophyll,phyto,oxygen,ph,phytoplankton,phosphate,silicate,salinity"

        payload = {}
        headers = {
          'Authorization': API_KEY
        }

        response = requests.request("GET", url_str, headers=headers, data = payload)
        response_dict = json.loads(response.text)    
        print("response_dict = ", response_dict)
        bio_dict = {}

        for hour_dict in response_dict['hours']:
    #         print("hour_dict = ", hour_dict)

            bio_dict['date'] = given_date
            for beach_col in beach_df.columns.tolist():
                bio_dict[beach_col] = row[beach_col]     

            bio_col_lst = list(hour_dict.keys())
            bio_col_lst.remove("time")

            for bio_col in bio_col_lst:

                bio_dict[bio_col] = hour_dict[bio_col]['sg']

            bio_dict['time'] = hour_dict['time']

            bio_df = bio_df.append(bio_dict, ignore_index=True)
###################################################################################################################


++++++++++++++++++++++++++++++++++++++++++++
api_limit =  0
api_no =  1
++++++++++++++++++++++++++++++++++++++++++++

index =  0
beach_name ADDISCOT BEACH
 
response_dict =  {'hours': [{'chlorophyll': {'mercator': 0.36, 'sg': 0.36}, 'iron': {'mercator': 0.0, 'sg': 0.0}, 'nitrate': {'mercator': 1.2, 'sg': 1.2}, 'oxygen': {'mercator': 251.8, 'sg': 251.8}, 'ph': {'mercator': 8.05, 'sg': 8.05}, 'phosphate': {'mercator': 0.33, 'sg': 0.33}, 'phyto': {'mercator': 5.42, 'sg': 5.42}, 'phytoplankton': {'mercator': 1.11, 'sg': 1.11}, 'silicate': {'mercator': 1.31, 'sg': 1.31}, 'time': '2020-06-05T00:00:00+00:00'}, {'chlorophyll': {'mercator': 0.36, 'sg': 0.36}, 'iron': {'mercator': 0.0, 'sg': 0.0}, 'nitrate': {'mercator': 1.2, 'sg': 1.2}, 'oxygen': {'mercator': 251.8, 'sg': 251.8}, 'ph': {'mercator': 8.05, 'sg': 8.05}, 'phosphate': {'mercator': 0.33, 'sg': 0.33}, 'phyto': {'mercator': 5.42, 'sg': 5.42}, 'phytoplankton': {'mercator': 1.11, 'sg': 1.11}, 'silicate': {'mercator': 1.31, 'sg': 1.31}, '

response_dict =  {'hours': [{'chlorophyll': {'mercator': 0.34, 'sg': 0.34}, 'iron': {'mercator': 0.0, 'sg': 0.0}, 'nitrate': {'mercator': 0.16, 'sg': 0.16}, 'oxygen': {'mercator': 250.84, 'sg': 250.84}, 'ph': {'mercator': 8.06, 'sg': 8.06}, 'phosphate': {'mercator': 0.25, 'sg': 0.25}, 'phyto': {'mercator': 6.09, 'sg': 6.09}, 'phytoplankton': {'mercator': 1.39, 'sg': 1.39}, 'silicate': {'mercator': 1.3, 'sg': 1.3}, 'time': '2020-06-05T00:00:00+00:00'}, {'chlorophyll': {'mercator': 0.34, 'sg': 0.34}, 'iron': {'mercator': 0.0, 'sg': 0.0}, 'nitrate': {'mercator': 0.16, 'sg': 0.16}, 'oxygen': {'mercator': 250.84, 'sg': 250.84}, 'ph': {'mercator': 8.06, 'sg': 8.06}, 'phosphate': {'mercator': 0.25, 'sg': 0.25}, 'phyto': {'mercator': 6.09, 'sg': 6.09}, 'phytoplankton': {'mercator': 1.38, 'sg': 1.38}, 'silicate': {'mercator': 1.3, 'sg': 1.3}, 'time': '2020-06-05T01:00:00+00:00'}, {'chlorophyll': {'mercator': 0.34, 'sg': 0.34}, 'iron': {'mercator': 0.0, 'sg': 0.0}, 'nitrate': {'mercator': 0.16, 

response_dict =  {'hours': [{'chlorophyll': {'mercator': 0.34, 'sg': 0.34}, 'iron': {'mercator': 0.0, 'sg': 0.0}, 'nitrate': {'mercator': 0.16, 'sg': 0.16}, 'oxygen': {'mercator': 250.84, 'sg': 250.84}, 'ph': {'mercator': 8.06, 'sg': 8.06}, 'phosphate': {'mercator': 0.25, 'sg': 0.25}, 'phyto': {'mercator': 6.09, 'sg': 6.09}, 'phytoplankton': {'mercator': 1.39, 'sg': 1.39}, 'silicate': {'mercator': 1.3, 'sg': 1.3}, 'time': '2020-06-05T00:00:00+00:00'}, {'chlorophyll': {'mercator': 0.34, 'sg': 0.34}, 'iron': {'mercator': 0.0, 'sg': 0.0}, 'nitrate': {'mercator': 0.16, 'sg': 0.16}, 'oxygen': {'mercator': 250.84, 'sg': 250.84}, 'ph': {'mercator': 8.06, 'sg': 8.06}, 'phosphate': {'mercator': 0.25, 'sg': 0.25}, 'phyto': {'mercator': 6.09, 'sg': 6.09}, 'phytoplankton': {'mercator': 1.38, 'sg': 1.38}, 'silicate': {'mercator': 1.3, 'sg': 1.3}, 'time': '2020-06-05T01:00:00+00:00'}, {'chlorophyll': {'mercator': 0.34, 'sg': 0.34}, 'iron': {'mercator': 0.0, 'sg': 0.0}, 'nitrate': {'mercator': 0.16, 

response_dict =  {'hours': [{'chlorophyll': {'mercator': 0.36, 'sg': 0.36}, 'iron': {'mercator': 0.0, 'sg': 0.0}, 'nitrate': {'mercator': 1.2, 'sg': 1.2}, 'oxygen': {'mercator': 251.8, 'sg': 251.8}, 'ph': {'mercator': 8.05, 'sg': 8.05}, 'phosphate': {'mercator': 0.33, 'sg': 0.33}, 'phyto': {'mercator': 5.42, 'sg': 5.42}, 'phytoplankton': {'mercator': 1.11, 'sg': 1.11}, 'silicate': {'mercator': 1.31, 'sg': 1.31}, 'time': '2020-06-05T00:00:00+00:00'}, {'chlorophyll': {'mercator': 0.36, 'sg': 0.36}, 'iron': {'mercator': 0.0, 'sg': 0.0}, 'nitrate': {'mercator': 1.2, 'sg': 1.2}, 'oxygen': {'mercator': 251.8, 'sg': 251.8}, 'ph': {'mercator': 8.05, 'sg': 8.05}, 'phosphate': {'mercator': 0.33, 'sg': 0.33}, 'phyto': {'mercator': 5.42, 'sg': 5.42}, 'phytoplankton': {'mercator': 1.11, 'sg': 1.11}, 'silicate': {'mercator': 1.31, 'sg': 1.31}, 'time': '2020-06-05T01:00:00+00:00'}, {'chlorophyll': {'mercator': 0.36, 'sg': 0.36}, 'iron': {'mercator': 0.0, 'sg': 0.0}, 'nitrate': {'mercator': 1.2, 'sg':

response_dict =  {'hours': [{'chlorophyll': {'mercator': 0.34, 'sg': 0.34}, 'iron': {'mercator': 0.0, 'sg': 0.0}, 'nitrate': {'mercator': 0.16, 'sg': 0.16}, 'oxygen': {'mercator': 250.84, 'sg': 250.84}, 'ph': {'mercator': 8.06, 'sg': 8.06}, 'phosphate': {'mercator': 0.25, 'sg': 0.25}, 'phyto': {'mercator': 6.09, 'sg': 6.09}, 'phytoplankton': {'mercator': 1.39, 'sg': 1.39}, 'silicate': {'mercator': 1.3, 'sg': 1.3}, 'time': '2020-06-05T00:00:00+00:00'}, {'chlorophyll': {'mercator': 0.34, 'sg': 0.34}, 'iron': {'mercator': 0.0, 'sg': 0.0}, 'nitrate': {'mercator': 0.16, 'sg': 0.16}, 'oxygen': {'mercator': 250.84, 'sg': 250.84}, 'ph': {'mercator': 8.06, 'sg': 8.06}, 'phosphate': {'mercator': 0.25, 'sg': 0.25}, 'phyto': {'mercator': 6.09, 'sg': 6.09}, 'phytoplankton': {'mercator': 1.38, 'sg': 1.38}, 'silicate': {'mercator': 1.3, 'sg': 1.3}, 'time': '2020-06-05T01:00:00+00:00'}, {'chlorophyll': {'mercator': 0.34, 'sg': 0.34}, 'iron': {'mercator': 0.0, 'sg': 0.0}, 'nitrate': {'mercator': 0.16, 

...

response_dict =  {'hours': [{'chlorophyll': {'mercator': 0.34, 'sg': 0.34}, 'iron': {'mercator': 0.0, 'sg': 0.0}, 'nitrate': {'mercator': 0.16, 'sg': 0.16}, 'oxygen': {'mercator': 250.84, 'sg': 250.84}, 'ph': {'mercator': 8.06, 'sg': 8.06}, 'phosphate': {'mercator': 0.25, 'sg': 0.25}, 'phyto': {'mercator': 6.09, 'sg': 6.09}, 'phytoplankton': {'mercator': 1.39, 'sg': 1.39}, 'silicate': {'mercator': 1.3, 'sg': 1.3}, 'time': '2020-06-05T00:00:00+00:00'}, {'chlorophyll': {'mercator': 0.34, 'sg': 0.34}, 'iron': {'mercator': 0.0, 'sg': 0.0}, 'nitrate': {'mercator': 0.16, 'sg': 0.16}, 'oxygen': {'mercator': 250.84, 'sg': 250.84}, 'ph': {'mercator': 8.06, 'sg': 8.06}, 'phosphate': {'mercator': 0.25, 'sg': 0.25}, 'phyto': {'mercator': 6.09, 'sg': 6.09}, 'phytoplankton': {'mercator': 1.38, 'sg': 1.38}, 'silicate': {'mercator': 1.3, 'sg': 1.3}, 'time': '2020-06-05T01:00:00+00:00'}, {'chlorophyll': {'mercator': 0.34, 'sg': 0.34}, 'iron': {'mercator': 0.0, 'sg': 0.0}, 'nitrate': {'mercator': 0.16, 

response_dict =  {'hours': [{'chlorophyll': {'mercator': 0.46, 'sg': 0.46}, 'iron': {'mercator': 0.0, 'sg': 0.0}, 'nitrate': {'mercator': 2.43, 'sg': 2.43}, 'oxygen': {'mercator': 249.6, 'sg': 249.6}, 'ph': {'mercator': 8.04, 'sg': 8.04}, 'phosphate': {'mercator': 0.27, 'sg': 0.27}, 'phyto': {'mercator': 10.18, 'sg': 10.18}, 'phytoplankton': {'mercator': 1.51, 'sg': 1.51}, 'silicate': {'mercator': 1.31, 'sg': 1.31}, 'time': '2020-06-05T00:00:00+00:00'}, {'chlorophyll': {'mercator': 0.47, 'sg': 0.47}, 'iron': {'mercator': 0.0, 'sg': 0.0}, 'nitrate': {'mercator': 2.43, 'sg': 2.43}, 'oxygen': {'mercator': 249.63, 'sg': 249.63}, 'ph': {'mercator': 8.04, 'sg': 8.04}, 'phosphate': {'mercator': 0.27, 'sg': 0.27}, 'phyto': {'mercator': 10.25, 'sg': 10.25}, 'phytoplankton': {'mercator': 1.52, 'sg': 1.52}, 'silicate': {'mercator': 1.31, 'sg': 1.31}, 'time': '2020-06-05T01:00:00+00:00'}, {'chlorophyll': {'mercator': 0.47, 'sg': 0.47}, 'iron': {'mercator': 0.0, 'sg': 0.0}, 'nitrate': {'mercator': 

response_dict =  {'hours': [], 'meta': {'cost': 1, 'dailyQuota': 50, 'end': '2020-06-06 00:00', 'lat': -35.8488, 'lng': 145.584, 'params': ['iron', 'nitrate', 'chlorophyll', 'phyto', 'oxygen', 'ph', 'phytoplankton', 'phosphate', 'silicate', 'salinity'], 'requestCount': 42, 'start': '2020-06-05 00:00'}}

index =  192
beach_name WILSONS BEACH
 
response_dict =  {'hours': [], 'meta': {'cost': 1, 'dailyQuota': 50, 'end': '2020-06-06 00:00', 'lat': -35.8688, 'lng': 145.602, 'params': ['iron', 'nitrate', 'chlorophyll', 'phyto', 'oxygen', 'ph', 'phytoplankton', 'phosphate', 'silicate', 'salinity'], 'requestCount': 43, 'start': '2020-06-05 00:00'}}

index =  193
beach_name WOODSIDE BEACH
 
response_dict =  {'hours': [{'chlorophyll': {'mercator': 0.42, 'sg': 0.42}, 'iron': {'mercator': 0.0, 'sg': 0.0}, 'nitrate': {'mercator': 0.14, 'sg': 0.14}, 'oxygen': {'mercator': 253.93, 'sg': 253.93}, 'ph': {'mercator': 8.06, 'sg': 8.06}, 'phosphate': {'mercator': 0.29, 'sg': 0.29}, 'phyto': {'mercator': 8

response_dict =  {'hours': [{'chlorophyll': {'mercator': 0.34, 'sg': 0.34}, 'iron': {'mercator': 0.0, 'sg': 0.0}, 'nitrate': {'mercator': 0.16, 'sg': 0.16}, 'oxygen': {'mercator': 250.84, 'sg': 250.84}, 'ph': {'mercator': 8.06, 'sg': 8.06}, 'phosphate': {'mercator': 0.25, 'sg': 0.25}, 'phyto': {'mercator': 6.09, 'sg': 6.09}, 'phytoplankton': {'mercator': 1.39, 'sg': 1.39}, 'silicate': {'mercator': 1.3, 'sg': 1.3}, 'time': '2020-06-05T00:00:00+00:00'}, {'chlorophyll': {'mercator': 0.34, 'sg': 0.34}, 'iron': {'mercator': 0.0, 'sg': 0.0}, 'nitrate': {'mercator': 0.16, 'sg': 0.16}, 'oxygen': {'mercator': 250.84, 'sg': 250.84}, 'ph': {'mercator': 8.06, 'sg': 8.06}, 'phosphate': {'mercator': 0.25, 'sg': 0.25}, 'phyto': {'mercator': 6.09, 'sg': 6.09}, 'phytoplankton': {'mercator': 1.38, 'sg': 1.38}, 'silicate': {'mercator': 1.3, 'sg': 1.3}, 'time': '2020-06-05T01:00:00+00:00'}, {'chlorophyll': {'mercator': 0.34, 'sg': 0.34}, 'iron': {'mercator': 0.0, 'sg': 0.0}, 'nitrate': {'mercator': 0.16, 

response_dict =  {'hours': [{'chlorophyll': {'mercator': 0.35, 'sg': 0.35}, 'iron': {'mercator': 0.0, 'sg': 0.0}, 'nitrate': {'mercator': 0.3, 'sg': 0.3}, 'oxygen': {'mercator': 253.79, 'sg': 253.79}, 'ph': {'mercator': 8.06, 'sg': 8.06}, 'phosphate': {'mercator': 0.29, 'sg': 0.29}, 'phyto': {'mercator': 6.74, 'sg': 6.74}, 'phytoplankton': {'mercator': 1.25, 'sg': 1.25}, 'silicate': {'mercator': 1.34, 'sg': 1.34}, 'time': '2020-06-05T00:00:00+00:00'}, {'chlorophyll': {'mercator': 0.35, 'sg': 0.35}, 'iron': {'mercator': 0.0, 'sg': 0.0}, 'nitrate': {'mercator': 0.31, 'sg': 0.31}, 'oxygen': {'mercator': 253.79, 'sg': 253.79}, 'ph': {'mercator': 8.06, 'sg': 8.06}, 'phosphate': {'mercator': 0.29, 'sg': 0.29}, 'phyto': {'mercator': 6.74, 'sg': 6.74}, 'phytoplankton': {'mercator': 1.25, 'sg': 1.25}, 'silicate': {'mercator': 1.34, 'sg': 1.34}, 'time': '2020-06-05T01:00:00+00:00'}, {'chlorophyll': {'mercator': 0.35, 'sg': 0.35}, 'iron': {'mercator': 0.0, 'sg': 0.0}, 'nitrate': {'mercator': 0.31

# CONVERT UTC TIME TO AUSTRALIA TIME:

In [18]:
bio_df['time'] = bio_df['time'].apply(lambda x: convert_datetime_in_dif_timezones(from_datetime_str = x, 
                                                                                  from_timezone_str = 'UTC', 
                                                                                  to_timezone_str ='Australia/Melbourne', 
                                                                                datetime_format = '%Y-%m-%dT%H:%M:%S+00:00'))

In [25]:
# bio_df.isnull().sum()
try:
    bio_df['ph'].fillna((bio_df['ph'].mean()), inplace=True)
except:
    pass

# CREATE SEA_WATER_QUALITY_TABLE:

In [26]:
import psycopg2 as ps

# define credentials 
credentials = {'POSTGRES_ADDRESS' : 'test-surfers-bible-instance.cljoljhkgpfb.ap-southeast-2.rds.amazonaws.com', # change to your endpoint
               'POSTGRES_PORT' : 5432, # change to your port
               'POSTGRES_USERNAME' : '', # change to your username
               'POSTGRES_PASSWORD' : '', # change to your password
               'POSTGRES_DBNAME' : 'test_surfers_bible_db'} # change to your db name

# create connection and cursor    
conn = ps.connect(host=credentials['POSTGRES_ADDRESS'],
                  database=credentials['POSTGRES_DBNAME'],
                  user=credentials['POSTGRES_USERNAME'],
                  password=credentials['POSTGRES_PASSWORD'],
                  port=credentials['POSTGRES_PORT'])

cur = conn.cursor()

# cur.execute("DROP TABLE SEA_WATER_QUALITY_TABLE;")

create_table_query = '''
      CREATE TABLE IF NOT EXISTS SEA_WATER_QUALITY_TABLE
      (
        sea_water_quality_id SERIAL PRIMARY KEY,
        date DATE,
        beach_id INTEGER,
        beach_name TEXT,
        beach_latitude REAL,
        beach_longitude REAL,
        beach_state  TEXT,
        beach_municipality TEXT,
        chlorophyll REAL,
        iron REAL,
        nitrate REAL,
        oxygen REAL,
        ph REAL,
        phosphate REAL,
        phyto REAL,
        phytoplankton REAL,
        salinity REAL,
        silicate REAL,
        time TEXT,
        FOREIGN KEY (beach_id) REFERENCES beach_table(beach_id) ON DELETE CASCADE
       ); 
       '''

cur.execute(create_table_query)
conn.commit()

# INSERT SEA_WATER_QUALITY_TABLE:

In [27]:
# %%time
# Wall time: 12min 51s
import psycopg2 as ps

# define credentials 
credentials = {'POSTGRES_ADDRESS' : 'test-surfers-bible-instance.cljoljhkgpfb.ap-southeast-2.rds.amazonaws.com', # change to your endpoint
               'POSTGRES_PORT' : 5432, # change to your port
               'POSTGRES_USERNAME' : '', # change to your username
               'POSTGRES_PASSWORD' : '', # change to your password
               'POSTGRES_DBNAME' : 'test_surfers_bible_db'} # change to your db name

# create connection and cursor    
conn = ps.connect(host=credentials['POSTGRES_ADDRESS'],
                  database=credentials['POSTGRES_DBNAME'],
                  user=credentials['POSTGRES_USERNAME'],
                  password=credentials['POSTGRES_PASSWORD'],
                  port=credentials['POSTGRES_PORT'])

cur = conn.cursor()

fill_question_mark_str = str(tuple(["%s"  for i in bio_df.columns.tolist()])).replace("'", "")
fill_question_mark_str

for row in bio_df.itertuples():
    data_tuple = tuple(row[1:])

    print("data_tuple = ", data_tuple)
    print(" ")
    
    cur.execute("""
                        INSERT INTO SEA_WATER_QUALITY_TABLE
                        (
                            date,
                            beach_id,
                            beach_name,
                            beach_latitude,
                            beach_longitude,
                            beach_state,
                            beach_municipality,
                            chlorophyll,
                            iron,
                            nitrate,
                            oxygen,
                            ph,
                            phosphate,
                            phyto,
                            phytoplankton,
                            salinity,
                            silicate,
                            time
                         ) VALUES  
                         """ + fill_question_mark_str + " ;"
                , data_tuple)    

conn.commit()
cur.close()
conn.close()

data_tuple =  ('2020-06-05', 1, 'ADDISCOT BEACH', -38.3823, 144.257, 'VIC', 'SURF COAST SHIRE', 0.36, 0.0, 1.2, 251.8, 8.05, 0.33, 5.42, 1.11, nan, 1.31, '2020-06-05T10:00:00')
 
data_tuple =  ('2020-06-05', 1, 'ADDISCOT BEACH', -38.3823, 144.257, 'VIC', 'SURF COAST SHIRE', 0.36, 0.0, 1.2, 251.8, 8.05, 0.33, 5.42, 1.11, nan, 1.31, '2020-06-05T11:00:00')
 
data_tuple =  ('2020-06-05', 1, 'ADDISCOT BEACH', -38.3823, 144.257, 'VIC', 'SURF COAST SHIRE', 0.36, 0.0, 1.2, 251.8, 8.05, 0.33, 5.41, 1.11, nan, 1.31, '2020-06-05T12:00:00')
 
data_tuple =  ('2020-06-05', 1, 'ADDISCOT BEACH', -38.3823, 144.257, 'VIC', 'SURF COAST SHIRE', 0.36, 0.0, 1.2, 251.8, 8.05, 0.33, 5.41, 1.11, nan, 1.31, '2020-06-05T13:00:00')
 
data_tuple =  ('2020-06-05', 1, 'ADDISCOT BEACH', -38.3823, 144.257, 'VIC', 'SURF COAST SHIRE', 0.36, 0.0, 1.2, 251.8, 8.05, 0.33, 5.41, 1.11, nan, 1.31, '2020-06-05T14:00:00')
 
data_tuple =  ('2020-06-05', 1, 'ADDISCOT BEACH', -38.3823, 144.257, 'VIC', 'SURF COAST SHIRE', 0.36, 0.0

data_tuple =  ('2020-06-05', 5, 'BARRY BEACH', -38.5176, 145.203, 'VIC', 'BASS COAST SHIRE', 0.34, 0.0, 0.17, 250.84, 8.06, 0.25, 6.13, 1.36, nan, 1.3, '2020-06-05T22:00:00')
 
data_tuple =  ('2020-06-05', 6, 'BARRYS BEACH', -38.5176, 145.203, 'VIC', 'BASS COAST SHIRE', 0.34, 0.0, 0.16, 250.84, 8.06, 0.25, 6.09, 1.39, nan, 1.3, '2020-06-05T10:00:00')
 
data_tuple =  ('2020-06-05', 6, 'BARRYS BEACH', -38.5176, 145.203, 'VIC', 'BASS COAST SHIRE', 0.34, 0.0, 0.16, 250.84, 8.06, 0.25, 6.09, 1.38, nan, 1.3, '2020-06-05T11:00:00')
 
data_tuple =  ('2020-06-05', 6, 'BARRYS BEACH', -38.5176, 145.203, 'VIC', 'BASS COAST SHIRE', 0.34, 0.0, 0.16, 250.84, 8.06, 0.25, 6.1, 1.38, nan, 1.3, '2020-06-05T12:00:00')
 
data_tuple =  ('2020-06-05', 6, 'BARRYS BEACH', -38.5176, 145.203, 'VIC', 'BASS COAST SHIRE', 0.34, 0.0, 0.16, 250.84, 8.06, 0.25, 6.1, 1.38, nan, 1.3, '2020-06-05T13:00:00')
 
data_tuple =  ('2020-06-05', 6, 'BARRYS BEACH', -38.5176, 145.203, 'VIC', 'BASS COAST SHIRE', 0.34, 0.0, 0.16, 25

data_tuple =  ('2020-06-05', 9, 'BELLS BEACH', -38.3688, 144.283, 'VIC', 'SURF COAST SHIRE', 0.35, 0.0, 1.2, 251.79, 8.05, 0.33, 5.4, 1.1, nan, 1.32, '2020-06-05T19:00:00')
 
data_tuple =  ('2020-06-05', 9, 'BELLS BEACH', -38.3688, 144.283, 'VIC', 'SURF COAST SHIRE', 0.35, 0.0, 1.2, 251.79, 8.05, 0.33, 5.4, 1.1, nan, 1.32, '2020-06-05T20:00:00')
 
data_tuple =  ('2020-06-05', 9, 'BELLS BEACH', -38.3688, 144.283, 'VIC', 'SURF COAST SHIRE', 0.35, 0.0, 1.2, 251.79, 8.05, 0.33, 5.4, 1.1, nan, 1.32, '2020-06-05T21:00:00')
 
data_tuple =  ('2020-06-05', 9, 'BELLS BEACH', -38.3688, 144.283, 'VIC', 'SURF COAST SHIRE', 0.35, 0.0, 1.2, 251.78, 8.05, 0.33, 5.4, 1.09, nan, 1.32, '2020-06-05T22:00:00')
 
data_tuple =  ('2020-06-05', 10, 'BERRY BEACH', -38.5176, 145.203, 'VIC', 'BASS COAST SHIRE', 0.34, 0.0, 0.16, 250.84, 8.06, 0.25, 6.09, 1.39, nan, 1.3, '2020-06-05T10:00:00')
 
data_tuple =  ('2020-06-05', 10, 'BERRY BEACH', -38.5176, 145.203, 'VIC', 'BASS COAST SHIRE', 0.34, 0.0, 0.16, 250.84, 8.

data_tuple =  ('2020-06-05', 13, 'BIRDROCK BEACH', -38.2493, 145.028, 'VIC', 'MORNINGTON PENINSULA SHIRE', 0.34, 0.0, 0.16, 250.84, 8.06, 0.25, 6.1, 1.38, nan, 1.3, '2020-06-05T14:00:00')
 
data_tuple =  ('2020-06-05', 13, 'BIRDROCK BEACH', -38.2493, 145.028, 'VIC', 'MORNINGTON PENINSULA SHIRE', 0.34, 0.0, 0.16, 250.84, 8.06, 0.25, 6.11, 1.38, nan, 1.3, '2020-06-05T15:00:00')
 
data_tuple =  ('2020-06-05', 13, 'BIRDROCK BEACH', -38.2493, 145.028, 'VIC', 'MORNINGTON PENINSULA SHIRE', 0.34, 0.0, 0.16, 250.84, 8.06, 0.25, 6.11, 1.37, nan, 1.3, '2020-06-05T16:00:00')
 
data_tuple =  ('2020-06-05', 13, 'BIRDROCK BEACH', -38.2493, 145.028, 'VIC', 'MORNINGTON PENINSULA SHIRE', 0.34, 0.0, 0.16, 250.84, 8.06, 0.25, 6.12, 1.37, nan, 1.3, '2020-06-05T17:00:00')
 
data_tuple =  ('2020-06-05', 13, 'BIRDROCK BEACH', -38.2493, 145.028, 'VIC', 'MORNINGTON PENINSULA SHIRE', 0.34, 0.0, 0.16, 250.84, 8.06, 0.25, 6.12, 1.37, nan, 1.3, '2020-06-05T18:00:00')
 
data_tuple =  ('2020-06-05', 13, 'BIRDROCK BEA

data_tuple =  ('2020-06-05', 29, 'CHERRY TREE BEACH', -37.9856, 147.652, 'VIC', 'EAST GIPPSLAND SHIRE', 0.49, 0.0, 0.09, 253.85, 8.07, 0.27, 8.24, 1.93, nan, 1.62, '2020-06-05T11:00:00')
 
data_tuple =  ('2020-06-05', 29, 'CHERRY TREE BEACH', -37.9856, 147.652, 'VIC', 'EAST GIPPSLAND SHIRE', 0.49, 0.0, 0.09, 253.86, 8.07, 0.27, 8.24, 1.93, nan, 1.62, '2020-06-05T12:00:00')
 
data_tuple =  ('2020-06-05', 29, 'CHERRY TREE BEACH', -37.9856, 147.652, 'VIC', 'EAST GIPPSLAND SHIRE', 0.49, 0.0, 0.09, 253.87, 8.07, 0.27, 8.23, 1.93, nan, 1.62, '2020-06-05T13:00:00')
 
data_tuple =  ('2020-06-05', 29, 'CHERRY TREE BEACH', -37.9856, 147.652, 'VIC', 'EAST GIPPSLAND SHIRE', 0.49, 0.0, 0.09, 253.87, 8.07, 0.27, 8.23, 1.93, nan, 1.62, '2020-06-05T14:00:00')
 
data_tuple =  ('2020-06-05', 29, 'CHERRY TREE BEACH', -37.9856, 147.652, 'VIC', 'EAST GIPPSLAND SHIRE', 0.49, 0.0, 0.09, 253.88, 8.07, 0.27, 8.22, 1.92, nan, 1.62, '2020-06-05T15:00:00')
 
data_tuple =  ('2020-06-05', 29, 'CHERRY TREE BEACH', -

...

data_tuple =  ('2020-06-05', 177, 'THIRTEENTH BEACH', -38.2845, 144.459, 'VIC', 'GREATER GEELONG CITY', 0.34, 0.0, 0.16, 250.84, 8.06, 0.25, 6.09, 1.38, nan, 1.3, '2020-06-05T11:00:00')
 
data_tuple =  ('2020-06-05', 177, 'THIRTEENTH BEACH', -38.2845, 144.459, 'VIC', 'GREATER GEELONG CITY', 0.34, 0.0, 0.16, 250.84, 8.06, 0.25, 6.1, 1.38, nan, 1.3, '2020-06-05T12:00:00')
 
data_tuple =  ('2020-06-05', 177, 'THIRTEENTH BEACH', -38.2845, 144.459, 'VIC', 'GREATER GEELONG CITY', 0.34, 0.0, 0.16, 250.84, 8.06, 0.25, 6.1, 1.38, nan, 1.3, '2020-06-05T13:00:00')
 
data_tuple =  ('2020-06-05', 177, 'THIRTEENTH BEACH', -38.2845, 144.459, 'VIC', 'GREATER GEELONG CITY', 0.34, 0.0, 0.16, 250.84, 8.06, 0.25, 6.1, 1.38, nan, 1.3, '2020-06-05T14:00:00')
 
data_tuple =  ('2020-06-05', 177, 'THIRTEENTH BEACH', -38.2845, 144.459, 'VIC', 'GREATER GEELONG CITY', 0.34, 0.0, 0.16, 250.84, 8.06, 0.25, 6.11, 1.38, nan, 1.3, '2020-06-05T15:00:00')
 
data_tuple =  ('2020-06-05', 177, 'THIRTEENTH BEACH', -38.2845,

data_tuple =  ('2020-06-05', 181, 'TIP BEACH', -37.5739, 149.759, 'VIC', 'EAST GIPPSLAND SHIRE', 0.44, 0.0, 0.63, 248.93, 8.09, 0.29, 7.19, 1.52, nan, 1.75, '2020-06-05T19:00:00')
 
data_tuple =  ('2020-06-05', 181, 'TIP BEACH', -37.5739, 149.759, 'VIC', 'EAST GIPPSLAND SHIRE', 0.45, 0.0, 0.62, 248.95, 8.09, 0.29, 7.21, 1.52, nan, 1.75, '2020-06-05T20:00:00')
 
data_tuple =  ('2020-06-05', 181, 'TIP BEACH', -37.5739, 149.759, 'VIC', 'EAST GIPPSLAND SHIRE', 0.45, 0.0, 0.62, 248.98, 8.09, 0.29, 7.23, 1.52, nan, 1.75, '2020-06-05T21:00:00')
 
data_tuple =  ('2020-06-05', 181, 'TIP BEACH', -37.5739, 149.759, 'VIC', 'EAST GIPPSLAND SHIRE', 0.45, 0.0, 0.62, 249.0, 8.09, 0.29, 7.26, 1.52, nan, 1.75, '2020-06-05T22:00:00')
 
data_tuple =  ('2020-06-05', 182, 'TOORA BEACH', -38.6913, 146.336, 'VIC', 'SOUTH GIPPSLAND SHIRE', 0.35, 0.0, 0.3, 253.79, 8.06, 0.29, 6.74, 1.25, nan, 1.34, '2020-06-05T10:00:00')
 
data_tuple =  ('2020-06-05', 182, 'TOORA BEACH', -38.6913, 146.336, 'VIC', 'SOUTH GIPPSLA

data_tuple =  ('2020-06-05', 188, 'WESTERN PARK BEACH', -38.398, 145.184, 'VIC', 'MORNINGTON PENINSULA SHIRE', 0.34, 0.0, 0.16, 250.84, 8.06, 0.25, 6.1, 1.38, nan, 1.3, '2020-06-05T14:00:00')
 
data_tuple =  ('2020-06-05', 188, 'WESTERN PARK BEACH', -38.398, 145.184, 'VIC', 'MORNINGTON PENINSULA SHIRE', 0.34, 0.0, 0.16, 250.84, 8.06, 0.25, 6.11, 1.38, nan, 1.3, '2020-06-05T15:00:00')
 
data_tuple =  ('2020-06-05', 188, 'WESTERN PARK BEACH', -38.398, 145.184, 'VIC', 'MORNINGTON PENINSULA SHIRE', 0.34, 0.0, 0.16, 250.84, 8.06, 0.25, 6.11, 1.37, nan, 1.3, '2020-06-05T16:00:00')
 
data_tuple =  ('2020-06-05', 188, 'WESTERN PARK BEACH', -38.398, 145.184, 'VIC', 'MORNINGTON PENINSULA SHIRE', 0.34, 0.0, 0.16, 250.84, 8.06, 0.25, 6.12, 1.37, nan, 1.3, '2020-06-05T17:00:00')
 
data_tuple =  ('2020-06-05', 188, 'WESTERN PARK BEACH', -38.398, 145.184, 'VIC', 'MORNINGTON PENINSULA SHIRE', 0.34, 0.0, 0.16, 250.84, 8.06, 0.25, 6.12, 1.37, nan, 1.3, '2020-06-05T18:00:00')
 
data_tuple =  ('2020-06-05

data_tuple =  ('2020-06-05', 191, 'WILD DOG SHORE', -38.1328, 147.339, 'VIC', 'WELLINGTON SHIRE', 0.49, 0.0, 0.09, 253.92, 8.07, 0.27, 8.18, 1.91, nan, 1.63, '2020-06-05T22:00:00')
 
data_tuple =  ('2020-06-05', 194, 'WOODSIDE BEACH', -38.5522, 146.978, 'VIC', 'WELLINGTON SHIRE', 0.42, 0.0, 0.14, 253.93, 8.06, 0.29, 8.89, 1.4, nan, 1.47, '2020-06-05T10:00:00')
 
data_tuple =  ('2020-06-05', 194, 'WOODSIDE BEACH', -38.5522, 146.978, 'VIC', 'WELLINGTON SHIRE', 0.42, 0.0, 0.14, 253.95, 8.06, 0.29, 8.89, 1.41, nan, 1.47, '2020-06-05T11:00:00')
 
data_tuple =  ('2020-06-05', 194, 'WOODSIDE BEACH', -38.5522, 146.978, 'VIC', 'WELLINGTON SHIRE', 0.42, 0.0, 0.14, 253.96, 8.06, 0.29, 8.89, 1.41, nan, 1.47, '2020-06-05T12:00:00')
 
data_tuple =  ('2020-06-05', 194, 'WOODSIDE BEACH', -38.5522, 146.978, 'VIC', 'WELLINGTON SHIRE', 0.42, 0.0, 0.14, 253.98, 8.06, 0.29, 8.9, 1.41, nan, 1.47, '2020-06-05T13:00:00')
 
data_tuple =  ('2020-06-05', 194, 'WOODSIDE BEACH', -38.5522, 146.978, 'VIC', 'WELLINGT

 
data_tuple =  ('2020-06-05', 197, 'WRECK BEACH', -38.7546, 143.212, 'VIC', 'CORANGAMITE SHIRE', 0.37, 0.0, 1.8, 250.02, 8.04, 0.29, 5.64, 1.15, nan, 1.25, '2020-06-05T18:00:00')
 
data_tuple =  ('2020-06-05', 197, 'WRECK BEACH', -38.7546, 143.212, 'VIC', 'CORANGAMITE SHIRE', 0.37, 0.0, 1.8, 250.02, 8.04, 0.29, 5.65, 1.15, nan, 1.25, '2020-06-05T19:00:00')
 
data_tuple =  ('2020-06-05', 197, 'WRECK BEACH', -38.7546, 143.212, 'VIC', 'CORANGAMITE SHIRE', 0.37, 0.0, 1.8, 250.02, 8.04, 0.29, 5.65, 1.15, nan, 1.25, '2020-06-05T20:00:00')
 
data_tuple =  ('2020-06-05', 197, 'WRECK BEACH', -38.7546, 143.212, 'VIC', 'CORANGAMITE SHIRE', 0.37, 0.0, 1.8, 250.03, 8.04, 0.29, 5.66, 1.15, nan, 1.25, '2020-06-05T21:00:00')
 
data_tuple =  ('2020-06-05', 197, 'WRECK BEACH', -38.7546, 143.212, 'VIC', 'CORANGAMITE SHIRE', 0.37, 0.0, 1.8, 250.03, 8.04, 0.29, 5.67, 1.15, nan, 1.25, '2020-06-05T22:00:00')
 
data_tuple =  ('2020-06-05', 198, 'YANAKIE BEACH', -38.8108, 146.269, 'VIC', 'SOUTH GIPPSLAND SHIR

___
___
___